In [1]:
# Импорт библиотек
from Def import *

In [2]:
# Читаем данные
df = pd.read_csv('df.csv')

# Переиндексация по столбцу времени
df['open_time'] = pd.to_datetime(df['open_time'])  # Предполагая, что столбец с временем называется 'time'
df.set_index('open_time', inplace=True)


In [3]:
top_adx = 0
lowest_adx = 0
top_DI_pos= 0
#Удаляем Nan
df.dropna(inplace=True)
# Устанавливаем начальное значение флага позиции
position = 'out'

# Создаем список для хранения сигналов
signals = [] # Сигналы
sc=[] # Счёт сделок
s=0 # Счёт сделок
b=0 # Вид/тип сделки
p=0 # Цена за покупку
top_p=0
low_stc=0
price=0 # Цена за сделку на покупку
b2_stop=0
# Проходим по строкам таблицы
for index, row in df.iterrows():
    #Helpfull stuff
    if row['ADX'] > 20 and row['ADX']>row['prev_adx']:
        top_adx=row['ADX']
    elif row['ADX'] < 20:
        top_adx=0
    if position == 'long':
        if row['close'] > row['prev_close']:
            top_p = row['close']
    else:
        top_p=0
    if row['ADX']>30 and row['diff_adx']>0:
        b2_stop=1
    
    # Условия покупки
    if position == 'out':
        if row['DI+'] - row['DI-'] > 2000 and row['diff_adx'] < 1 and row['diff_adx'] > -1 and row['diff_close'] > 0.0037 and row['diff_close'] < 0.008:
            b=1
            s+=1
            sc.append(s)
            p=row['close']
            print(s,b,p,row['diff_close2'],row['diff_close'],row['diff_adx'],row['turnover'])
            signals.append('buy')
            position = 'long'
        elif row['stc'] < 35 and row['diff_rsi4']>-10 and row['%K']>30 and row['signal_line']<-20 and row['STC']>0:
            b=2
            s+=1
            sc.append(s)
            p=row['close']
            print(s,b,p,row['diff_adx'],row['diff_rsi4'])
            signals.append('buy')
            price = row['close']
            position = 'long'
        elif row['DI+'] - row['DI-'] > 15 and row['DI+'] > row['prev_di_plus'] and row['ADX'] > 2000 and row['diff_adx'] > 2.5 and row ['volume'] > 4*10**6 and row['diff_close2'] > 80 and row['volume']<20:
            b=3
            s+=1
            sc.append(s)
            p=row['close']
            print(s,b,p,row['diff_close2'],row['diff_close'],row['diff_adx'],row['turnover'])
            signals.append('buy')
            position = 'long'
        else:
            signals.append('hold')
            sc.append(None)
            price = 0

    # Условия продажи
    elif position == 'long':
        if b==1:
                if ((top_p - row['close'])/row['close'])*100>0.3:
                    signals.append('sell')
                    sc.append(s)
                    position = 'out'
                elif top_adx - row['ADX']>15:
                    signals.append('sell')
                    sc.append(s)
                    position = 'out'
                elif row['DI-'] > row['DI+']:
                    signals.append('sell')
                    sc.append(s)
                    position = 'out'
                else:
                    signals.append('hold')
                    sc.append(None)
        if b==2:
                if ((top_p - row['close'])/row['close'])*100>0.5:
                    signals.append('sell')
                    sc.append(s)
                    position = 'out'
                else:
                    signals.append('hold')
                    sc.append(None)
        elif b==3:
                if top_adx - row['ADX']>15:
                    signals.append('sell')
                    sc.append(s)
                    position = 'out'
                elif row['DI-'] > row['DI+']:
                    signals.append('sell')
                    sc.append(s)
                    position = 'out'
                else:
                    signals.append('hold')
                    sc.append(None)
                    
# Создаем столбец с сигналами
df['signal'] = signals
df['score'] = sc

1 2 27043.0 -0.3079069324282102 67.75
2 2 27358.5 -0.5681417364203405 50.125
3 2 27738.0 -1.668495920737211 -6.375
4 2 27152.5 -0.9456418763418633 35.25
5 2 27413.0 -1.0214947264088785 -3.25
6 2 27422.5 -3.685835014011897 47.25
7 2 26929.5 -0.975910159170553 16.625
8 2 27913.0 -1.238590865716997 78.875
9 2 28405.5 -0.3735239106484762 61.625
10 2 28259.0 -0.5889967678787187 59.625
11 2 27687.5 -0.3188516106798609 47.625
12 2 28204.5 -1.4668018741591131 72.5
13 2 28097.5 -1.8534271767593395 65.5
14 2 28032.0 0.1399847385644221 40.375
15 2 27913.5 0.569325876476622 -5.625
16 2 28002.0 1.090466473956237 45.125
17 2 30163.0 0.9301277673304932 58.75
18 2 29990.0 0.1138066306470015 39.5
19 2 29224.5 -1.3033326397167642 9.5
20 2 27956.5 -0.6102673413145343 40.625
21 2 27336.5 -0.1168497992917316 67.625
22 2 27462.5 -1.7655552772173913 7.875
23 2 27314.0 -0.4975726166215573 87.375


In [4]:
# Выводим результаты
initial_cash = 1000
commission = 0.0001
days = 60
calculate_profit(df, initial_cash, commission, days)

initial_cash2: 1000
Profit: $ 115.05627884981436
Total Trades: 22
Successful Trades: 13
Unsuccessful Trades: 9
Win Rate: 59.09%
commission: 0.0001
days: 60


In [5]:
make_graf(df)